![dvd_image](dvd_image.jpg)

A DVD rental company needs your help! They want to figure out how many days a customer will rent a DVD for based on some features and has approached you for help. They want you to try out some regression models which will help predict the number of days a customer will rent a DVD for. The company wants a model which yeilds a MSE of 3 or less on a test set. The model you make will help the company become more efficient inventory planning.

The data they provided is in the csv file `rental_info.csv`. It has the following features:
- `"rental_date"`: The date (and time) the customer rents the DVD.
- `"return_date"`: The date (and time) the customer returns the DVD.
- `"amount"`: The amount paid by the customer for renting the DVD.
- `"amount_2"`: The square of `"amount"`.
- `"rental_rate"`: The rate at which the DVD is rented for.
- `"rental_rate_2"`: The square of `"rental_rate"`.
- `"release_year"`: The year the movie being rented was released.
- `"length"`: Lenght of the movie being rented, in minuites.
- `"length_2"`: The square of `"length"`.
- `"replacement_cost"`: The amount it will cost the company to replace the DVD.
- `"special_features"`: Any special features, for example trailers/deleted scenes that the DVD also has.
- `"NC-17"`, `"PG"`, `"PG-13"`, `"R"`: These columns are dummy variables of the rating of the movie. It takes the value 1 if the move is rated as the column name and 0 otherwise. For your convinience, the reference dummy has already been dropped.

In [130]:
import pandas as pd
import numpy as np

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from sklearn.tree import DecisionTreeRegressor
from sklearn.linear_model import LinearRegression , Ridge , Lasso
from sklearn.svm import SVR
from sklearn.ensemble import VotingRegressor

# Import any additional modules and start coding below
df = pd.read_csv('rental_info.csv')

df

rental_date  ... rental_rate_2
0      2005-05-25 02:54:33+00:00  ...        8.9401
1      2005-06-15 23:19:16+00:00  ...        8.9401
2      2005-07-10 04:27:45+00:00  ...        8.9401
3      2005-07-31 12:06:41+00:00  ...        8.9401
4      2005-08-19 12:30:04+00:00  ...        8.9401
...                          ...  ...           ...
15856  2005-08-22 10:49:15+00:00  ...       24.9001
15857  2005-07-31 09:48:49+00:00  ...       24.9001
15858  2005-08-20 10:35:30+00:00  ...       24.9001
15859  2005-07-31 13:10:20+00:00  ...       24.9001
15860  2005-08-18 06:33:55+00:00  ...       24.9001

[15861 rows x 15 columns]

In [131]:
df.isna().sum()

rental_date         0
return_date         0
amount              0
release_year        0
rental_rate         0
length              0
replacement_cost    0
special_features    0
NC-17               0
PG                  0
PG-13               0
R                   0
amount_2            0
length_2            0
rental_rate_2       0
dtype: int64

In [132]:
newdf = df
newdf['rental_date'] = pd.to_datetime(newdf['rental_date'])
newdf["return_date"] = pd.to_datetime(newdf["return_date"])
newdf

rental_date  ... rental_rate_2
0     2005-05-25 02:54:33+00:00  ...        8.9401
1     2005-06-15 23:19:16+00:00  ...        8.9401
2     2005-07-10 04:27:45+00:00  ...        8.9401
3     2005-07-31 12:06:41+00:00  ...        8.9401
4     2005-08-19 12:30:04+00:00  ...        8.9401
...                         ...  ...           ...
15856 2005-08-22 10:49:15+00:00  ...       24.9001
15857 2005-07-31 09:48:49+00:00  ...       24.9001
15858 2005-08-20 10:35:30+00:00  ...       24.9001
15859 2005-07-31 13:10:20+00:00  ...       24.9001
15860 2005-08-18 06:33:55+00:00  ...       24.9001

[15861 rows x 15 columns]

In [133]:
x = (newdf['return_date'] - newdf['rental_date']).dt.days
x

0        3
1        2
2        7
3        2
4        4
        ..
15856    6
15857    4
15858    9
15859    8
15860    6
Length: 15861, dtype: int64

In [134]:
newdf['rental_length_days'] = x
newdf

rental_date  ... rental_length_days
0     2005-05-25 02:54:33+00:00  ...                  3
1     2005-06-15 23:19:16+00:00  ...                  2
2     2005-07-10 04:27:45+00:00  ...                  7
3     2005-07-31 12:06:41+00:00  ...                  2
4     2005-08-19 12:30:04+00:00  ...                  4
...                         ...  ...                ...
15856 2005-08-22 10:49:15+00:00  ...                  6
15857 2005-07-31 09:48:49+00:00  ...                  4
15858 2005-08-20 10:35:30+00:00  ...                  9
15859 2005-07-31 13:10:20+00:00  ...                  8
15860 2005-08-18 06:33:55+00:00  ...                  6

[15861 rows x 16 columns]

In [135]:
dummies = newdf
dummies['deleted_scenes'] = dummies["special_features"].str.contains( 'Deleted Scenes').astype(int)
dummies['behind_the_scenes'] = dummies["special_features"].str.contains( 'Behind the Scenes').astype(int)
dummies

rental_date  ... behind_the_scenes
0     2005-05-25 02:54:33+00:00  ...                 1
1     2005-06-15 23:19:16+00:00  ...                 1
2     2005-07-10 04:27:45+00:00  ...                 1
3     2005-07-31 12:06:41+00:00  ...                 1
4     2005-08-19 12:30:04+00:00  ...                 1
...                         ...  ...               ...
15856 2005-08-22 10:49:15+00:00  ...                 1
15857 2005-07-31 09:48:49+00:00  ...                 1
15858 2005-08-20 10:35:30+00:00  ...                 1
15859 2005-07-31 13:10:20+00:00  ...                 1
15860 2005-08-18 06:33:55+00:00  ...                 1

[15861 rows x 18 columns]

In [136]:
dummies['special_features'].value_counts()

{Trailers,Commentaries,"Behind the Scenes"}                     1308
{Trailers}                                                      1139
{Trailers,Commentaries}                                         1129
{Trailers,"Behind the Scenes"}                                  1122
{"Behind the Scenes"}                                           1108
{Commentaries,"Deleted Scenes","Behind the Scenes"}             1101
{Commentaries}                                                  1089
{Commentaries,"Behind the Scenes"}                              1078
{Trailers,"Deleted Scenes"}                                     1047
{"Deleted Scenes","Behind the Scenes"}                          1035
{"Deleted Scenes"}                                              1023
{Commentaries,"Deleted Scenes"}                                 1011
{Trailers,Commentaries,"Deleted Scenes","Behind the Scenes"}     983
{Trailers,Commentaries,"Deleted Scenes"}                         916
{Trailers,"Deleted Scenes","Behind

In [137]:
dummies['deleted_scenes'].value_counts()

0    7973
1    7888
Name: deleted_scenes, dtype: int64

In [138]:
#X = dummies[['amount' , 'release_year' , 'rental_rate' , 'length' , 'replacement_cost' , '']]
X = dummies
X = X.drop(columns=['special_features', 'rental_date' , 'return_date' , 'rental_length_days'] , axis = 1)
X

amount  release_year  ...  deleted_scenes  behind_the_scenes
0        2.99        2005.0  ...               0                  1
1        2.99        2005.0  ...               0                  1
2        2.99        2005.0  ...               0                  1
3        2.99        2005.0  ...               0                  1
4        2.99        2005.0  ...               0                  1
...       ...           ...  ...             ...                ...
15856    6.99        2009.0  ...               1                  1
15857    4.99        2009.0  ...               1                  1
15858    8.99        2009.0  ...               1                  1
15859    7.99        2009.0  ...               1                  1
15860    5.99        2009.0  ...               1                  1

[15861 rows x 14 columns]

In [139]:
y = dummies['rental_length_days']
y

0        3
1        2
2        7
3        2
4        4
        ..
15856    6
15857    4
15858    9
15859    8
15860    6
Name: rental_length_days, Length: 15861, dtype: int64

In [140]:
X_train , X_test , y_train , y_test = train_test_split(X , y , test_size = 0.2 , random_state = 9)

In [141]:
lr = LinearRegression()
dtr = DecisionTreeRegressor()
ridge = Ridge()
lasso = Lasso()
svr = SVR()

In [142]:
regressors = [('Linear Regression', lr), ('Decision Tree Regressor', dtr), ('Ridge', ridge) ,  ('Lasso' , lasso) , ('Support Vector Regressor' , svr)]
vr = VotingRegressor(estimators = regressors)

In [143]:
vr.fit(X_train , y_train)
y_pred = vr.predict(X_test)
mse = mean_squared_error(y_test , y_pred)
mse

2.8238081260575623

In [144]:
dict = {}
for name , model in regressors:
    model.fit(X_train , y_train)
    y_pred_model = model.predict(X_test)
    mse_model = mean_squared_error(y_test , y_pred_model)
    dict[name] = mse_model

dict

{'Linear Regression': 2.9417238646975883,
 'Decision Tree Regressor': 2.170930163313851,
 'Ridge': 2.9417585460802016,
 'Lasso': 3.8056884092652106,
 'Support Vector Regressor': 7.140934567092472}

In [145]:
best_model = DecisionTreeRegressor()
best_mse = dict['Decision Tree Regressor']